In [2]:
!pip install google_patent_scraper

Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/share/pkg.7/python3/3.8.6/install/bin/python3.8 -m pip install --upgrade pip' command.


In [3]:
from google_patent_scraper import scraper_class
from bs4 import BeautifulSoup

In [4]:
import csv
import json

In [5]:
with open("2006_CN_KR_patent_grant_processed.csv", 'r',encoding="utf8") as file:
    csvreader = csv.reader(file)

    count = 0

    for row in csvreader:

        if count==0:
            print(len(row))

        count+=1

        if count<20:
            print(row)
        
print(count)

21
['', 'publication_id', 'publication_kind', 'publication_date', 'application_id', 'application_date', 'country', 'inventor_name', 'inventor_firstname', 'inventor_country', 'invention_title', 'number_of_claims', 'attorney_name', 'attorney_firstname', 'inventor males', 'inventor females', 'inventor team size', 'attorney males', 'attorney females', 'attorney team size', 'Year']
['2', 'US06982341', 'B1', '20060103', 'US11093995', '20050330', 'US', "['Kim Yunsoo', 'Kim Chang Gyoun', 'Chung Taek-Mo', 'Lee Sun Sook', 'An Ki-Seok', 'Yang Taek Seung', 'Jang Hong Suk']", "['Yunsoo', 'Chang Gyoun', 'Taek-Mo', 'Sun Sook', 'Ki-Seok', 'Taek Seung', 'Hong Suk']", "['KR', 'KR', 'KR', 'KR', 'KR', 'KR', 'KR']", 'Volatile copper aminoalkoxide complex and deposition of copper thin film using same', '6', '[]', '[]', '6', '1', '7', '0', '0', '0', '2006']
['10', 'US06982347', 'B2', '20060103', 'US10806460', '20040323', 'DE', "['Dieterle Martin', 'Petzoldt Jochen', 'Müller-Engel Klaus Joachim', 'Arnold Heik

In [6]:
with open("2020_CN_KR_patent_grant_processed.csv", 'r',encoding="utf8") as file:
    csvreader = csv.reader(file)

    count = 0

    for row in csvreader:

        if count==0:
            print(len(row))

        count+=1

        if count<20:
            print(row)
        
print(count)

21
['', 'publication_id', 'publication_kind', 'publication_date', 'application_id', 'application_date', 'country', 'inventor_name', 'inventor_firstname', 'inventor_country', 'invention_title', 'number_of_claims', 'attorney_name', 'attorney_firstname', 'inventor males', 'inventor females', 'inventor team size', 'attorney males', 'attorney females', 'attorney team size', 'Year']
['8', 'US10529746', 'B2', '20200107', 'US16106826', '20180821', 'KR', "['Bae Sung-hwan', 'Oh Seunghee', 'Kim Joonhyeong', 'Song Younggoo']", "['Sung-hwan', 'Seunghee', 'Joonhyeong', 'Younggoo']", "['KR', 'KR', 'KR', 'KR']", 'Display panel including external conductive pad, display apparatus including the same and method of manufacturing the same', '19', '[]', '[]', '1', '3', '4', '0', '0', '0', '2020']
['9', 'US10529747', 'B2', '20200107', 'US16184075', '20181108', 'KR', "['Han Se Hee', 'Kim Tae Gyun']", "['Se Hee', 'Tae Gyun']", "['KR', 'KR']", 'Display device', '9', '[]', '[]', '2', '0', '2', '0', '0', '0', '20

In [7]:
def return_cn_kr_numbers(number):
    
    if len(number)==0:
        return ["No Application Number"], ["No Application Number"]
    
    if number[0:4] == "USD0":
        number = number.replace('0', '', 1)
    elif number[0:3] == "US0":
        number = number.replace('0', '', 1)
    
    # ~ Initialize scraper class ~ #
    scraper=scraper_class()

    # ~~ Scrape patents individually ~~ #
    err, soup, url = scraper.request_single_patent(number)
    
    if err==404:
        return ["Patent not found"], ["Patent not found"]

    app_by_year = soup.find_all('li', itemprop='applicationsByYear')

    apps = []
    for x in app_by_year:
        ap = x.find_all('li', itemprop='application')
        apps = apps + ap

    patents = []
    #urls = []
    
    print(len(apps))

    for y in apps:
        if y.find_all('span',itemprop='countryCode')[0].text == 'CN' or y.find_all('span',itemprop='countryCode')[0].text == 'KR':
            url = y.find_all('span',itemprop='documentId')[0].text
            #urls.append(url)
            patents.append(url[7:])

    #print(urls)
    print(patents)
    #print("\n")
    
    if len(patents)==0:
        return ["No KR or CN Application Number"], ["No KR or CN Application Number"]
    
    names = []
    
    for p in patents:

        err_a, soup_a, url_a = scraper.request_single_patent(p)

        # ~ Parse results of scrape ~ #
        patent_p = scraper.get_scraped_data(soup_a,p,url_a)

        n = []
        
        # ~ Print inventors of patents ~ 
        for inventor in json.loads(patent_p['inventor_name']):
            #print('Patent inventor : {0}'.format(inventor['inventor_name']))
            n.append(inventor['inventor_name'])
        
        names.append(n)
    print(names)

    print("\n")
    return patents, names

In [8]:
cn_kr_patents_rows = []

with open("2020_CN_KR_patent_grant_processed.csv", 'r',encoding="utf8") as file:
    csvreader = csv.reader(file)
    
    cn_kr_patents_rows = []
    
    count = 0

    for row in csvreader:
        
        if count%100==0 and count>0:
            with open("2020_CN_KR_patent_grant_processed_names.csv", mode='a', newline='',encoding="utf8") as file_3:
                writer = csv.writer(file_3)
                writer.writerows(cn_kr_patents_rows)
                print(count)
                print("="*50+"SAVED"+"="*50)
                cn_kr_patents_rows = []

        if count==0:
            
            row.append("WorldWide Applications")
            row.append("Original Names")
            
            cn_kr_patents_rows.append(row)
            
            print(len(row))
            print(row)
            print("\n\n")
            count+=1
            continue
        
        try:
            patents, names = return_cn_kr_numbers(row[1])
        except Exception as e:
            print(e)
            patents, names = [str(e)], [str(e)]
        
        row.append(patents)
        row.append(names)
        
        print(count,"\n\n")
        
        count+=1
        
        cn_kr_patents_rows.append(row)


        #if count<20:
        #    print(row)

if len(cn_kr_patents_rows)>0:
    with open("2020_CN_KR_patent_grant_processed_names.csv", mode='a', newline='',encoding="utf8") as file_3:
        writer = csv.writer(file_3)
        writer.writerows(cn_kr_patents_rows)
        print(count)
        print("="*50+"SAVED"+"="*50)
        cn_kr_patents_rows = []

23
['', 'publication_id', 'publication_kind', 'publication_date', 'application_id', 'application_date', 'country', 'inventor_name', 'inventor_firstname', 'inventor_country', 'invention_title', 'number_of_claims', 'attorney_name', 'attorney_firstname', 'inventor males', 'inventor females', 'inventor team size', 'attorney males', 'attorney females', 'attorney team size', 'Year', 'WorldWide Applications', 'Original Names']



https://patents.google.com/patent/US10529746
5
['KR20170139211A/en', 'CN107479229A/en']
https://patents.google.com/patent/KR20170139211A/en
https://patents.google.com/patent/CN107479229A/en
[['배성환', '오승희', '김준형', '송영구'], ['裵盛焕', '吴昇禧', '金俊亨', '宋荣九']]


1 


https://patents.google.com/patent/US10529747
6
['KR102392471B1/en']
https://patents.google.com/patent/KR102392471B1/en
[['한세희', '김태균']]


2 


https://patents.google.com/patent/US10529749
1
[]
3 


https://patents.google.com/patent/US10529750
5
['CN104882415B/en']
https://patents.google.com/patent/CN104882415B/en


3
['KR102368033B1/en', 'CN109524542A/en']
https://patents.google.com/patent/KR102368033B1/en
https://patents.google.com/patent/CN109524542A/en
[['조한나', '윤혜지', '권오익'], ['赵汉娜', '尹惠智', '权五益']]


41 


https://patents.google.com/patent/US10529929
6
['KR102419178B1/en', 'CN106935712A/en', 'KR20220095177A/en']
https://patents.google.com/patent/KR102419178B1/en
https://patents.google.com/patent/CN106935712A/en
https://patents.google.com/patent/KR20220095177A/en
[['조환희', '김명숙', '김희연', '추창웅'], ['赵桓熙', '金明淑', '金喜妍', '秋昌雄'], ['김명숙', '조환희', '김희연', '추창웅']]


42 


https://patents.google.com/patent/US10529933
6
['KR102292768B1/en', 'CN108137564A/en']
https://patents.google.com/patent/KR102292768B1/en
https://patents.google.com/patent/CN108137564A/en
[['안희춘'], ['安熙春']]


43 


https://patents.google.com/patent/US10529935
2
['KR20170094650A/en']
https://patents.google.com/patent/KR20170094650A/en
[['이지연', '곽윤현', '권오현', '이선영', '최현호', '김지환']]


44 


https://patents.google.com/patent/US10529936
3
['KR20

2
['KR101740041B1/en']
https://patents.google.com/patent/KR101740041B1/en
[['강승택']]


80 


https://patents.google.com/patent/US10530066
7
['KR20170087753A/en', 'CN108604726B/en']
https://patents.google.com/patent/KR20170087753A/en
https://patents.google.com/patent/CN108604726B/en
[['이영주', '김현진', '박정민'], ['李永周', '金贤珍', '朴正敏']]


81 


https://patents.google.com/patent/US10530099
5
['KR101926504B1/en', 'CN109980384B/en']
https://patents.google.com/patent/KR101926504B1/en
https://patents.google.com/patent/CN109980384B/en
[['송화윤', '이진욱', '차선화', '양창현', '김은정', '정경훈', '정희석'], ['宋和伦', '李镇旭', '车善花', '杨昌弦', '金恩妌', '郑敬勋', '郑熙锡']]


82 


https://patents.google.com/patent/US10530102
5
['CN107210570A/en']
https://patents.google.com/patent/CN107210570A/en
[['张科', '蔡升有', '邓以实']]


83 


https://patents.google.com/patent/US10530104
3
['CN106981795B/en']
https://patents.google.com/patent/CN106981795B/en
[['张玉俊', '张莉', '沈宏伟']]


84 


https://patents.google.com/patent/US10524717
2
['CN107582081B/en']
h

https://patents.google.com/patent/CN115085786A/en
[['赵培尧', '王昭诚', '竺旭东', '陈晋辉'], ['赵培尧', '王昭诚', '竺旭东', '陈晋辉'], ['赵培尧', '王昭诚', '竺旭东', '陈晋辉']]


119 


https://patents.google.com/patent/US10524744
Patent: US10524744, Error Status Code : 404
120 


https://patents.google.com/patent/US10530443
4
['KR102360496B1/en', 'CN109004993B/en']
https://patents.google.com/patent/KR102360496B1/en
https://patents.google.com/patent/CN109004993B/en
[['이한엽', '양동일', '손봉섭', '이동주', '최원진', '나효석'], ['李汉烨', '梁东一', '孙凤涉', '李东柱', '崔元震', '罗孝锡']]


121 


https://patents.google.com/patent/US10530449
17
['CN104301014B/en', 'CN104202128B/en', 'CN102870362B/en']
https://patents.google.com/patent/CN104301014B/en
https://patents.google.com/patent/CN104202128B/en
https://patents.google.com/patent/CN102870362B/en
[['马蒂尔斯·费伦内', '刘江华'], ['马蒂尔斯·费伦内', '刘江华'], ['马蒂尔斯·费伦内', '刘江华']]


122 


https://patents.google.com/patent/USD871871
1
[]
123 


https://patents.google.com/patent/US10530450
5
['CN106559121B/en']
https://patents.

[['陆伟', '米而科·施拉姆']]


154 


https://patents.google.com/patent/US10530592
4
['CN103678367A/en']
https://patents.google.com/patent/CN103678367A/en
[['薄川川', '李美娜', '侯杰']]


155 


https://patents.google.com/patent/US10530593
7
['CN105519072B/en', 'CN107534566B/en']
https://patents.google.com/patent/CN105519072B/en
https://patents.google.com/patent/CN107534566B/en
[['程抒一', '周爱国', '周全', '崔颖哲', '朱天堃', '袁正'], ['程抒一', '袁正', '崔颖哲', '周全', '朱天堃', '周爱国']]


156 


https://patents.google.com/patent/US10530595
8
['KR102075957B1/en', 'CN105900355B/en']
https://patents.google.com/patent/KR102075957B1/en
https://patents.google.com/patent/CN105900355B/en
[['시펭 추', '준 왕', '시아오시아 창', '강 바오'], ['朱西鹏', '王俊', '张晓霞', 'G·包']]


157 


https://patents.google.com/patent/US10530596
4
['CN107820218B/en']
https://patents.google.com/patent/CN107820218B/en
[['杨亚', '张�林', '陈永兴']]


158 


https://patents.google.com/patent/US10530609
3
['KR20180076055A/en']
https://patents.google.com/patent/KR20180076055A/en
[['김진호', 

...

https://patents.google.com/patent/KR102180353B1/en
[['吴昊'], ['하오 우']]


54985 


https://patents.google.com/patent/US10878437
3
['CN105338066B/en']
https://patents.google.com/patent/CN105338066B/en
[['叶娃', '徐震宇', '李培库', '朱洲玮', '周梦莎', '林炯超', '吴蓓琪', '王利凯', '林建东', '卓达城', '连泽祺', '王泓扬']]


54986 


https://patents.google.com/patent/US10878461
3
['CN106504025B/en']
https://patents.google.com/patent/CN106504025B/en
[['王倩', '金奇', '杨臣俊', '陈争云', '郑灿', '陈俊良', '李雯姬', '张晓璐', '唐少刚', '李惠娟', '李轶昆']]


54987 


https://patents.google.com/patent/US10878479
1
[]
54988 


https://patents.google.com/patent/US10878488
3
[]
54989 


https://patents.google.com/patent/US10874218
2
['CN209965760U/en']
https://patents.google.com/patent/CN209965760U/en
[['陈礼斌', '孔庆磊', '蔡兴仪']]


54990 


https://patents.google.com/patent/US10878525
6
['CN109997346A/en']
https://patents.google.com/patent/CN109997346A/en
[['张凌宇']]


54991 


https://patents.google.com/patent/US10878530
2
['CN109242944A/en']
https://patents.google.co

4
['KR20170050718A/en', 'CN106652927B/en']
https://patents.google.com/patent/KR20170050718A/en
https://patents.google.com/patent/CN106652927B/en
[['김병우', '유상희'], ['金炳佑', '柳尚希']]


55030 


https://patents.google.com/patent/US10878766
2
['KR20180015309A/en']
https://patents.google.com/patent/KR20180015309A/en
[['온원종', '김영진', '김택영', '이준범', '하재민']]


55031 


https://patents.google.com/patent/US10878768
2
['KR20190096469A/en']
https://patents.google.com/patent/KR20190096469A/en
[['오관영', '김윤구', '박석진', '이원희', '한상수', '이재한']]


55032 


https://patents.google.com/patent/US10878774
2
['KR20190115547A/en']
https://patents.google.com/patent/KR20190115547A/en
[['임태곤', '김명수', '김보연', '강선구', '김용범', '박동원', '조정환']]


55033 


https://patents.google.com/patent/US10878777
2
['KR20170031322A/en']
https://patents.google.com/patent/KR20170031322A/en
[['황경호', '김영섭', '김지태']]


55034 


https://patents.google.com/patent/US10878779
1
[]
55035 


https://patents.google.com/patent/US10878780
2
['CN109036331B/en'

3
['CN109599412B/en']
https://patents.google.com/patent/CN109599412B/en
[['刘汝浩', '刘长洪', '范守善']]


55071 


https://patents.google.com/patent/USD905927
1
[]
55072 


https://patents.google.com/patent/US10879020
4
['CN106997818B/en']
https://patents.google.com/patent/CN106997818B/en
[['赵克龙', '雷鹏飞', '杨平']]


55073 


https://patents.google.com/patent/US10879026
3
['CN113035669A/en']
https://patents.google.com/patent/CN113035669A/en
[['杨心翮', '柳鹏', '范守善']]


55074 


https://patents.google.com/patent/US10879036
4
['CN106525845A/en']
https://patents.google.com/patent/CN106525845A/en
[['何伟', '李帅', '王鹏']]


55075 


https://patents.google.com/patent/US10879063
2
['CN110224020A/en']
https://patents.google.com/patent/CN110224020A/en
[['倪贤锋', '范谦', '何伟']]


55076 


https://patents.google.com/patent/US10879084
7
['KR20170067875A/en', 'CN106796894A/en']
https://patents.google.com/patent/KR20170067875A/en
https://patents.google.com/patent/CN106796894A/en
[['윈 류', '유화 이', '청성 쿠', '칭밍 류', '멍밍 주', '두산

https://patents.google.com/patent/CN111463238A/en
[['이민수', '박용성', '기원장', '노대현', '이승빈'], ['李旻洙', '朴镕盛', '奇源章', '卢大铉', '李承傧']]


55110 


https://patents.google.com/patent/US10879317
8
['KR102444177B1/en', 'CN106935713B/en', 'CN113410406A/en']
https://patents.google.com/patent/KR102444177B1/en
https://patents.google.com/patent/CN106935713B/en
https://patents.google.com/patent/CN113410406A/en
[['윤원민', '김이수', '박응석', '이병덕', '정윤아', '조윤형', '주용찬'], ['尹元珉', '金利受', '朴应皙', '李炳德', '郑允雅', '赵尹衡', '朱容赞'], ['尹元珉', '金利受', '朴应皙', '李炳德', '郑允雅', '赵尹衡', '朱容赞']]


55111 


https://patents.google.com/patent/US10879319
5
['KR20200032291A/en', 'CN110911449A/en']
https://patents.google.com/patent/KR20200032291A/en
https://patents.google.com/patent/CN110911449A/en
[['방기호', '이성룡', '전상현'], ['方琪皓', '李省龙', '全相炫']]


55112 


https://patents.google.com/patent/US10879320
2
['CN110061044B/en']
https://patents.google.com/patent/CN110061044B/en
[['朱鹏娟', '熊志勇', '鹿旭']]


55113 


https://patents.google.com/patent/US1087932

https://patents.google.com/patent/KR102394425B1/en
[['李恩庆', '郑知永', '朴正一', '崔雅净'], ['이은경', '정지영', '박정일', '최아정']]


55147 


https://patents.google.com/patent/US10879476
2
['KR102233811B1/en']
https://patents.google.com/patent/KR102233811B1/en
[['임경근']]


55148 


https://patents.google.com/patent/US10879478
3
['CN110391333A/en']
https://patents.google.com/patent/CN110391333A/en
[['宁文', '柳鹏', '姜开利', '范守善']]


55149 


https://patents.google.com/patent/US10879480
5
['KR20200081966A/en', 'CN111383599B/en']
https://patents.google.com/patent/KR20200081966A/en
https://patents.google.com/patent/CN111383599B/en
[['심주성', '홍무경'], ['沈柱成', '洪茂庆']]


55150 


https://patents.google.com/patent/US10879481
7
['KR102420453B1/en', 'CN106531894B/en', 'KR20220103077A/en']
https://patents.google.com/patent/KR102420453B1/en
https://patents.google.com/patent/CN106531894B/en
https://patents.google.com/patent/KR20220103077A/en
[['박은정'], ['朴银贞'], ['박은정']]


55151 


https://patents.google.com/patent/US10879484
6

In [ ]:
"""cn_kr_patents_rows = []

with open("2006_CN_KR_patent_grant_processed.csv", 'r',encoding="utf8") as file:
    csvreader = csv.reader(file)
    
    cn_kr_patents_rows = []
    
    count = 0

    for row in csvreader:
        
        if count%100==0 and count>0:
            with open("2006_CN_KR_patent_grant_processed_names.csv", mode='a', newline='',encoding="utf8") as file_3:
                writer = csv.writer(file_3)
                writer.writerows(cn_kr_patents_rows)
                print(count)
                print("="*50+"SAVED"+"="*50)
                cn_kr_patents_rows = []

        if count==0:
            
            row.append("WorldWide Applications")
            row.append("Original Names")
            
            cn_kr_patents_rows.append(row)
            
            print(len(row))
            print(row)
            print("\n\n")
            count+=1
            continue
        
        try:
            patents, names = return_cn_kr_numbers(row[1])
        except Exception as e:
            print(e)
            patents, names = [str(e)], [str(e)]
        
        row.append(patents)
        row.append(names)
        
        print(count,"\n\n")
        
        count+=1
        
        cn_kr_patents_rows.append(row)


        #if count<20:
        #    print(row)

if len(cn_kr_patents_rows)>0:
    with open("2006_CN_KR_patent_grant_processed_names.csv", mode='a', newline='',encoding="utf8") as file_3:
        writer = csv.writer(file_3)
        writer.writerows(cn_kr_patents_rows)
        print(count)
        print("="*50+"SAVED"+"="*50)
        cn_kr_patents_rows = []"""
print()

In [9]:
with open("2020_CN_KR_patent_grant_processed_names.csv", 'r',encoding="utf8") as file:
    csvreader = csv.reader(file)

    count = 0

    for row in csvreader:

        if count==0:
            print(len(row))

        count+=1

        if count<20:
            print(row)
        
print(count)

23
['', 'publication_id', 'publication_kind', 'publication_date', 'application_id', 'application_date', 'country', 'inventor_name', 'inventor_firstname', 'inventor_country', 'invention_title', 'number_of_claims', 'attorney_name', 'attorney_firstname', 'inventor males', 'inventor females', 'inventor team size', 'attorney males', 'attorney females', 'attorney team size', 'Year', 'WorldWide Applications', 'Original Names']
['8', 'US10529746', 'B2', '20200107', 'US16106826', '20180821', 'KR', "['Bae Sung-hwan', 'Oh Seunghee', 'Kim Joonhyeong', 'Song Younggoo']", "['Sung-hwan', 'Seunghee', 'Joonhyeong', 'Younggoo']", "['KR', 'KR', 'KR', 'KR']", 'Display panel including external conductive pad, display apparatus including the same and method of manufacturing the same', '19', '[]', '[]', '1', '3', '4', '0', '0', '0', '2020', "['KR20170139211A/en', 'CN107479229A/en']", "[['배성환', '오승희', '김준형', '송영구'], ['裵盛焕', '吴昇禧', '金俊亨', '宋荣九']]"]
['9', 'US10529747', 'B2', '20200107', 'US16184075', '20181108'